In [2]:
import modin.pandas as pd
from pyspark.sql import SparkSession
from pyspark.ml.evaluation import RegressionEvaluator
from pyspark.ml.recommendation import ALS
from pyspark.mllib.recommendation import ALS as newALS
from sklearn.metrics import mean_squared_error
from pyspark.sql.functions import *
from pyspark.sql.types import *
import numpy as np

In [3]:
path = "../../Downloads/ml-1m"

def split_data(path, sep):  
    df = pd.read_csv(f'{path}/ratings.dat', sep = sep, names=['user_id', 'movie_id', 'rating', 'timestamp']).sort_values('timestamp')
    start_ts = df['timestamp'].min()
    med_ts = df['timestamp'].quantile(.5)
    end_ts = df['timestamp'].max()
    train_df = df[df['timestamp'] <= med_ts]
    stream_df = df[df['timestamp'] > med_ts]
    '''
    seen_movies = set(train_df['movie_id'])
    print(len(seen_movies), len(set(stream_df['movie_id'])), len(stream_df))
    stream_df = stream_df.drop(stream_df[stream_df['movie_id'].map(lambda x: x not in seen_movies)].index)
    print(len(set(stream_df['movie_id'])), len(stream_df))
    seen_users = set(train_df['user_id'])
    num_stream_users = set(stream_df['user_id'])
    stream_df = stream_df.drop(stream_df[stream_df['user_id'].map(lambda x: x not in seen_users)].index)
    print(len(seen_users), len(num_stream_users), len(set(stream_df['user_id'])), len(stream_df))
    '''
    #train_df.to_csv(f'{path}/train.csv', header=True, index = False)
    #stream_df.to_csv(f'{path}/stream.csv', header=True, index = False)
    return start_ts, med_ts, end_ts

In [4]:
split_data(path, "::")

To remove this warning, run the following python code before doing dataframe operations:

    import ray
    ray.init()

To request implementation, send an email to feature_requests@modin.org.


(956703932, 973018006.0, 1046454590)

In [5]:
spark = SparkSession.builder.master('local').appName('als').getOrCreate()

Using Spark's default log4j profile: org/apache/spark/log4j-defaults.properties
Setting default log level to "WARN".
To adjust logging level use sc.setLogLevel(newLevel). For SparkR, use setLogLevel(newLevel).
22/03/15 11:47:12 WARN NativeCodeLoader: Unable to load native-hadoop library for your platform... using builtin-java classes where applicable


In [6]:
spark_df = spark.read.options(delimiter=",", inferSchema=True, header=True).csv(f'{path}/train.csv')

In [7]:
spark_df.show()

+-------+--------+------+---------+
|user_id|movie_id|rating|timestamp|
+-------+--------+------+---------+
|   6040|     858|     4|956703932|
|   6040|    2384|     4|956703954|
|   6040|     593|     5|956703954|
|   6040|    1961|     4|956703977|
|   6040|    2019|     5|956703977|
|   6040|    1419|     3|956704056|
|   6040|     213|     5|956704056|
|   6040|    3111|     5|956704056|
|   6040|     573|     4|956704056|
|   6040|    3505|     4|956704056|
|   6040|    1734|     2|956704081|
|   6040|    2503|     5|956704191|
|   6040|     919|     5|956704191|
|   6040|     912|     5|956704191|
|   6040|     527|     5|956704219|
|   6040|    1252|     5|956704257|
|   6040|     649|     5|956704257|
|   6040|     318|     4|956704257|
|   6040|    3289|     5|956704305|
|   6040|     759|     5|956704448|
+-------+--------+------+---------+
only showing top 20 rows



In [8]:
spark_df = spark_df.drop('timestamp')
spark_df.show()
new_model = newALS.train(ratings = spark_df.rdd, rank = 150, iterations=15, lambda_=.2)

+-------+--------+------+
|user_id|movie_id|rating|
+-------+--------+------+
|   6040|     858|     4|
|   6040|    2384|     4|
|   6040|     593|     5|
|   6040|    1961|     4|
|   6040|    2019|     5|
|   6040|    1419|     3|
|   6040|     213|     5|
|   6040|    3111|     5|
|   6040|     573|     4|
|   6040|    3505|     4|
|   6040|    1734|     2|
|   6040|    2503|     5|
|   6040|     919|     5|
|   6040|     912|     5|
|   6040|     527|     5|
|   6040|    1252|     5|
|   6040|     649|     5|
|   6040|     318|     4|
|   6040|    3289|     5|
|   6040|     759|     5|
+-------+--------+------+
only showing top 20 rows



22/03/15 11:47:20 WARN InstanceBuilder$NativeBLAS: Failed to load implementation from:dev.ludovic.netlib.blas.JNIBLAS
22/03/15 11:47:20 WARN InstanceBuilder$NativeBLAS: Failed to load implementation from:dev.ludovic.netlib.blas.ForeignLinkerBLAS
22/03/15 11:47:20 WARN InstanceBuilder$NativeLAPACK: Failed to load implementation from:dev.ludovic.netlib.lapack.JNILAPACK


In [9]:
spark_df.sort("user_id").show()

+-------+--------+------+
|user_id|movie_id|rating|
+-------+--------+------+
|   2783|     541|     4|
|   2783|    3927|     3|
|   2783|     750|     5|
|   2783|    1097|     3|
|   2783|     260|     4|
|   2783|     208|     1|
|   2783|    1199|     3|
|   2783|    2111|     3|
|   2783|    1214|     4|
|   2783|    1270|     4|
|   2783|     589|     5|
|   2783|    1210|     3|
|   2783|    1243|     3|
|   2783|    1200|     4|
|   2783|    1077|     5|
|   2783|     741|     5|
|   2783|    3702|     3|
|   2783|    1301|     5|
|   2783|    3471|     3|
|   2783|    2968|     5|
+-------+--------+------+
only showing top 20 rows



In [10]:
user_features = new_model.userFeatures().toDF().toPandas()
user_features = user_features.rename(columns={'_1': 'id', '_2': 'features'}).sort_values("id")
user_features

22/03/15 11:48:54 WARN BlockManager: Task 49 already completed, not releasing lock for rdd_321_0


id                                           features
0     2783  [-0.07469388097524643, -0.11229582130908966, -...
1     2784  [-0.08663611114025116, -0.010234715417027473, ...
2     2785  [-0.032865673303604126, -0.008891520090401173,...
3     2786  [-0.0562487356364727, -0.06679890304803848, -0...
4     2787  [-0.06586312502622604, -0.06487643718719482, -...
...    ...                                                ...
3250  6036  [-0.04556586593389511, -0.11425884813070297, 0...
3251  6037  [-0.05084821954369545, -0.07124742120504379, -...
3252  6038  [-0.004150833003222942, -0.046171560883522034,...
3253  6039  [-0.026292433962225914, -0.058327674865722656,...
3254  6040  [-0.04643099382519722, -0.15823514759540558, 0...

[3255 rows x 2 columns]

In [11]:
product_features = new_model.productFeatures().toDF().toPandas()
product_features = product_features.rename(columns={'_1': 'id', '_2': 'features'})

22/03/15 11:48:55 WARN BlockManager: Task 51 already completed, not releasing lock for rdd_322_0


In [12]:
product_features.sort_values('id').to_csv(f'{path}/movie_features.csv', index = False)
user_features.sort_values('id').to_csv(f'{path}/user_features.csv', index = False)

In [13]:
def get_feature_dict(features):
    feature_dict = dict()
    for row in features.itertuples():
        feature_dict[int(row.id)] = np.array(row.features)
    return feature_dict

In [14]:
user_dict = get_feature_dict(user_features)
movie_dict = get_feature_dict(product_features)  

In [15]:
new_user_dict = get_feature_dict(user_features)
new_movie_dict = get_feature_dict(product_features)  

In [16]:
stream_df = pd.read_csv(f'{path}/stream.csv')
stream_df['user_id'] = stream_df['user_id'].astype(int)

def predict_rating(row):
    if row.movie_id not in movie_dict:
        movie_dict[row.movie_id] = np.zeros(150)
    if row.user_id not in user_dict:
        return -1
        user_dict[row.user_id] = np.zeros(150)
        return -1
    movie_feature = movie_dict[row.movie_id]
    user_feature = user_dict[row.user_id]
    return user_feature.dot(movie_feature.T)

def predict_table(df):
    df['prediction'] = df.apply(predict_rating , axis=1)
    return df

In [17]:
prediction_df = predict_table(stream_df)

In [22]:
sans_new = prediction_df[prediction_df['prediction'] != -1]
mean_squared_error(sans_new['rating'], sans_new['prediction'])

0.9636635490536786

In [23]:
class FIFOScheduler:
    
    def __init__(self):
        self.queue = []
        
    def push(self, row):
        self.queue.append(row)
    
    def pop(self):
        if len(self.queue) == 0:
            return None
        return self.queue.pop()

In [20]:
class LeastUpdatedScheduler:
    
    def __init__():
        self.queue =

SyntaxError: invalid syntax (3544257431.py, line 4)

In [24]:
stream_df['timestamp'].max() - stream_df['timestamp'].min(), len(stream_df)

(73436566, 500104)

In [55]:
class SGDUpdater:
    
    def __init__(self, user_features, product_features, learning_rate, u_reg, m_reg, update_movies = True):
        self.user_dict = get_feature_dict(user_features)
        self.movie_dict = get_feature_dict(product_features) 
        self.l = learning_rate
        self.u_reg = u_reg
        self.m_reg = m_reg
        self.update_movies = update_movies
    
    def predict(self, row):
        movie_id = row.movie_id
        user_id = row.user_id
        
        if movie_id not in self.movie_dict:
            return -1
            self.movie_dict[movie_id] = np.random.rand(150)      
        if user_id not in self.user_dict:
            return -1
            self.user_dict[user_id] = np.random.rand(150)
        
        return self.user_dict[user_id].dot(self.movie_dict[movie_id].T)
    
    def update(self, row):
        movie_id = row.movie_id
        user_id = row.user_id
        rating = row.rating
        
        if movie_id not in self.movie_dict or user_id not in self.user_dict:
            return
        
        prediction = self.predict(row)
        error = rating - prediction
        
        
        self.user_dict[user_id] = self.user_dict[user_id] + self.l * (error * self.movie_dict[movie_id] - self.u_reg  * self.user_dict[user_id])
        if self.update_movies:
            self.movie_dict[movie_id] = self.movie_dict[movie_id] + self.l * (error * self.user_dict[user_id] - self.m_reg * self.movie_dict[movie_id])

In [27]:
data_to_send = dict()
for ts in stream_df['timestamp'].unique():
    curr_data = stream_df[stream_df['timestamp'] == ts]
    data_to_send[ts] = curr_data

(apply_list_of_funcs pid=47866) 
(compute_sliced_len pid=47866) 


(compute_sliced_len pid=47864) 
(apply_list_of_funcs pid=47861) 
(apply_list_of_funcs pid=47860) 
(apply_list_of_funcs pid=47865) 
(compute_sliced_len pid=47864) 
(compute_sliced_len pid=47867) 
(apply_list_of_funcs pid=47866) 
(apply_list_of_funcs pid=47865) 


(compute_sliced_len pid=47865) 


(apply_list_of_funcs pid=47866) 
(apply_list_of_funcs pid=47860) 
(compute_sliced_len pid=47859) 
(apply_list_of_funcs pid=47865) 
(apply_list_of_funcs pid=47859) 
(compute_sliced_len pid=47865) 
(compute_sliced_len pid=47866) 
(apply_list_of_funcs pid=47862) 
(compute_sliced_len pid=47863) 
(apply_list_of_funcs pid=47864) 
(apply_list_of_funcs pid=47862) 


(compute_sliced_len pid=47860) 


...

(apply_list_of_funcs pid=48465) 


(compute_sliced_len pid=48465) 


(apply_list_of_funcs pid=48465) 
(apply_list_of_funcs pid=48299) 
(apply_list_of_funcs pid=48408) 
(apply_list_of_funcs pid=48402) 


(apply_list_of_funcs pid=48320) 


(apply_list_of_funcs pid=48308) 


In [56]:
def simulate(scheduler, updater, data, feature_update_cadence, num_process):
    ts_range = sorted(data.keys())
    #ts = df['timestamp'].min()
    #end_ts = df['timestamp'].max()
    
    predictions = []
    next_feature_update_time = ts_range[0] + feature_update_cadence
    num_updates = 0
    num_processed = 0
    
    for ts in ts_range:
        curr_data = data[ts]
        #print(curr_data)
        print(num_processed)
        for row in curr_data.itertuples():
            scheduler.push(row)
            predictions.append(updater.predict(row))
        num_processed += len(curr_data)
        if ts >= next_feature_update_time:
            # how many records to process
            for i in range(num_process):
                row = scheduler.pop()
                if row:
                    updater.update(row)
                    num_updates += 1
            next_feature_update_time += feature_update_cadence
    '''
    while ts <= end_ts:
        # stream in data
        curr_data = df[df['timestamp'] == ts]
        
        if (num_processed + len(curr_data)) // 10 > num_processed // 10:
            print(num_processed)
        
        for row in curr_data.itertuples():
            scheduler.push(row)
            predictions.append(updater.predict(row))
        
        num_processed += len(curr_data)
        
        if ts == next_feature_update_time:
            # how many records to process
            for i in range(num_process):
                row = scheduler.pop()
                if row:
                    updater.update(row)
                    num_updates += 1
            next_feature_update_time += feature_update_cadence
             
        ts += 1
    '''
    print(num_updates)
    return predictions
    

In [57]:
sched = FIFOScheduler()
updater = SGDUpdater(user_features, product_features, .02, .01, .01)

import time
curr = time.time()
predictions = simulate(sched, updater, data_to_send, 100, 10)
print(time.time - curr)

0
2
3
4
6
7
8
10
11
12
14
18
19
21
22
24
25
28
30
31
34
36
40
42
45
47
49
51
52
54
57
58
60
64
65
69
71
72
74
75
79
82
84
87
89
93
96
98
100
103
104
108
111
114
119
122
123
124
126
127
128
129
133
134
136
139
143
144
147
150
151
153
156
158
160
162
165
167
169
171
174
176
178
185
186
188
191
193
194
197
198
200
201
203
206
209
210
211
213
214
215
216
217
218
219
220
221
224
226
229
230
235
238
239
244
247
248
250
251
255
257
259
263
264
266
270
278
281
282
284
285
288
290
294
295
299
301
303
304
305
310
311
312
313
315
317
319
323
326
329
332
333
335
337
339
340
341
344
345
346
348
350
352
355
356
358
360
362
366
367
369
372
373
374
375
377
378
379
380
382
385
386
387
389
392
396
400
402
405
407
408
410
411
412
415
418
422
424
427
429
431
434
435
437
438
439
442
443
445
447
448
454
456
459
460
462
463
465
466
470
472
474
477
481
482
483
485
487
488
490
491
492
496
498
500
505
506
508
510
515
517
519
520
524
526
531
534
535
537
538
539
543
545
546
547
549
551
554
555
559
561
566
567
568

(apply_list_of_funcs pid=48371) 


1578
1579
1580
1584
1589
1593
1595
1596
1597
1598
1600
1601
1602
1603
1604
1605
1606
1609
1611
1613
1616
1618
1620
1621
1623
1624
1625
1628
1631
1632
1633
1634
1635
1637
1638
1642
1643
1645
1649
1650
1651
1652
1653
1655
1656
1662
1663
1665
1667
1669
1673
1676
1678
1680
1682
1684
1685
1687
1688
1689
1693
1694
1695
1698
1699
1700
1703
1705
1707
1708
1710
1712
1716
1722
1725
1727
1729
1732
1736
1740
1743
1746
1748
1750
1753
1756
1759
1764
1765
1766
1769
1770
1773
1777
1779
1781
1784
1786
1788
1793
1795
1798
1800
1803
1806
1808
1810
1815
1816
1818
1819
1821
1823
1825
1827
1831
1833
1835
1836
1837
1841
1844
1846
1848
1849
1852
1854
1855
1858
1859
1860
1861
1864
1865
1867
1870
1872
1873
1876
1878
1880
1882
1884
1887
1890
1892
1894
1895
1897
1898
1899
1902
1904
1906
1908
1911
1912
1913
1914
1915
1916
1920
1922
1923
1926
1927
1928
1929
1932
1933
1935
1937
1939
1941
1947
1948
1953
1954
1957
1959
1961
1965
1970
1972
1977
1982
1984
1987
1990
1992
1993
1994
1997
1999
2001
2002
2003
2004
2007
2010


(compute_sliced_len pid=48464) 


4146
4147
4152
4155
4159
4160
4162
4163
4165
4167
4171
4174
4177
4180
4183
4184
4189
4191
4195
4198
4201
4205
4206
4208
4211
4215
4218
4221
4224
4226
4228
4230
4231
4232
4236
4238
4239
4240
4241
4244
4246
4249
4251
4253
4255
4256
4258
4259
4261
4262
4263
4264
4265
4266
4267
4268
4269
4270
4272
4273
4278
4279
4281
4282
4283
4284
4286
4287
4288
4291
4293
4294
4295
4297
4298
4299
4301
4304
4305
4310
4311
4314
4318
4320
4323
4325
4327
4330
4334
4338
4339
4343
4345
4346
4347
4348
4350
4354
4356
4361
4363
4364
4366
4371
4372
4373
4375
4381
4382
4386
4387
4393
4394
4399
4400
4408
4414
4419
4421
4424
4426
4435
4436
4437
4442
4450
4451
4452
4453
4460
4462
4464
4469
4471
4474
4475
4480
4482
4487
4491
4496
4498
4502
4504
4510
4512
4514
4515
4522
4523
4526
4532
4535
4536
4539
4545
4548
4551
4558
4559
4564
4566
4567
4574
4576
4579
4582
4583
4586
4587
4594
4597
4598
4600
4605
4608
4611
4612
4613
4614
4615
4620
4621
4623
4628
4629
4631
4636
4639
4640
4642
4649
4651
4655
4656
4659
4661
4665
4673
4675


...

22/03/15 16:12:54 WARN HeartbeatReceiver: Removing executor driver with no recent heartbeats: 131815 ms exceeds timeout 120000 ms
22/03/15 16:12:54 WARN SparkContext: Killing executors is not supported by current scheduler.


496645
496646
496647
496648
496649
496650
496652
496653
496654
496655
496656
496657
496658
496659
496662
496663
496667
496670
496674
496678
496679
496680
496681
496682
496684
496688
496692
496698
496704
496705
496708
496709
496710
496711
496712
496713
496715
496716
496717
496718
496719
496720
496721
496722
496723
496724
496725
496726
496729
496730
496731
496732
496733
496734
496735
496736
496737
496739
496740
496741
496743
496745
496746
496748
496749
496750
496751
496752
496754
496756
496757
496758
496759
496760
496761
496762
496763
496764
496765
496766
496768
496769
496770
496771
496772
496773
496778
496779
496780
496781
496782
496783
496784
496785
496786
496787
496788
496789
496790
496794
496795
496796
496797
496800
496802
496803
496805
496806
496807
496808
496809
496810
496816
496823
496831
496833
496836
496838
496839
496840
496841
496842
496844
496845
496846
496847
496850
496854
496857
496858
496859
496860
496862
496864
496865
496868
496871
496872
496873
496874
496875
496876
496877

498294
498296
498298
498302
498304
498305
498306
498310
498312
498314
498317
498318
498320
498321
498322
498324
498326
498329
498331
498334
498337
498339
498340
498341
498343
498347
498348
498349
498351
498352
498353
498356
498357
498358
498359
498360
498362
498365
498367
498369
498374
498378
498380
498384
498386
498387
498388
498389
498393
498396
498398
498399
498400
498402
498404
498405
498407
498409
498411
498412
498414
498418
498421
498424
498425
498428
498431
498432
498433
498434
498435
498436
498438
498440
498441
498442
498443
498444
498446
498448
498449
498450
498453
498458
498463
498464
498469
498470
498471
498472
498473
498475
498478
498482
498484
498485
498487
498489
498490
498493
498495
498496
498497
498498
498499
498500
498503
498505
498506
498507
498508
498509
498511
498513
498514
498515
498517
498518
498520
498522
498524
498525
498526
498527
498529
498530
498531
498532
498533
498535
498536
498537
498538
498540
498541
498542
498543
498544
498545
498546
498547
498548
498549

500051
500052
500053
500054
500055
500057
500059
500061
500062
500063
500065
500067
500068
500069
500071
500072
500073
500074
500075
500076
500077
500078
500079
500081
500082
500083
500084
500085
500086
500087
500088
500089
500090
500091
500092
500093
500094
500095
500096
500097
500098
500099
500100
500101
500103
500104


TypeError: unsupported operand type(s) for -: 'builtin_function_or_method' and 'float'

In [61]:
stream_df['predictions'] = predictions


user_id  movie_id  rating   timestamp  prediction  predictions
3          3970      2890       4   973018153    3.356627     3.393901
171        2784       608       5   973021691    3.547614     3.793208
172        2784      1259       5   973021691    3.576579     3.807878
173        2784      2858       5   973021691    3.750439     4.001544
200        2784      3408       3   973021816    3.410957     3.661493
...         ...       ...     ...         ...         ...          ...
500099     4958      2399       1  1046454338    2.397113     2.297596
500100     4958      1407       5  1046454443    3.179136     2.916980
500101     4958      3264       4  1046454548    2.845697     3.169769
500102     4958      2634       3  1046454548    2.887716     2.812283
500103     4958      1924       4  1046454590    2.307750     2.248052

[47595 rows x 6 columns]

In [62]:
stream_df.rename(columns={'prediction': 'pre_train_predictions'},inplace=True)

In [69]:
stream_df_measure = stream_df[stream_df['predictions'] != -1]
mean_squared_error(stream_df_measure['rating'], stream_df_measure['predictions'])

0.7819961804231305

In [70]:
mean_squared_error(stream_df_measure['rating'], stream_df_measure['pre_train_predictions'])

0.8943480271996258